In [1]:
!pip install wordfreq
!git clone https://github.com/awslabs/mlm-scoring.git
!pip install -e mlm-scoring/
!pip install torch mxnet-cu101mkl
!pip install language_tool_python

DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
Cloning into 'mlm-scoring'...
remote: Enumerating objects: 163, done.
remote: Counting objects: 100% (7/7), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 163 (delta 0), reused 3 (delta 0), pack-reused 156
Receiving objects: 100% (163/163), 23.50 MiB | 7.38 MiB/s, done.
Resolving deltas: 100% (68/68), done.
DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a H

  Created wheel for mosestokenizer: filename=mosestokenizer-1.2.1-py3-none-any.whl size=49191 sha256=12cc615fc6b479408c40906ab4608dd503b3d335b04b1ac07748f0baecf29a8b
  Stored in directory: /Users/gt/Library/Caches/pip/wheels/ae/81/8c/f39c59a230a9fa1075a884d3d2e63f5f0fc246525b61754543
  Created wheel for docopt: filename=docopt-0.6.2-py2.py3-none-any.whl size=13705 sha256=17b4d1e2293fe14288da82b8e4d903d310fe8198cfc7f81b8d6796b0572feaf0
  Stored in directory: /Users/gt/Library/Caches/pip/wheels/4e/29/5e/e5f6f558e24e0d70f6808e3e8fdaf2c04ff597233098afc550
  Created wheel for sacremoses: filename=sacremoses-0.0.53-py3-none-any.whl size=895254 sha256=79b4dc8e4dffc5e96655e44dd6a7220bff0a69548ea2533dc4a48f4c5e9d822a
  Stored in directory: /Users/gt/Library/Caches/pip/wheels/42/79/78/5ad3b042cb2d97c294535162cdbaf9b167e3b186eae55ab72d
  Created wheel for toolwrapper: filename=toolwrapper-2.1.0-py3-none-any.whl size=3353 sha256=d99c372b65aa1933161db10d87debde8e6a05f2308ec4cba7f96c926e0f056c1
  St

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive/')
WORK_PATH = "/content/gdrive/My Drive/TMaze"
%cd /content/mlm-scoring/src
from mlm.scorers import MLMScorer, MLMScorerPT, LMScorer 
from mlm.models import get_pretrained
import mxnet as mx
import pickle
import wordfreq
import string
from scipy.stats import norm
import spacy
import numpy as np #shouldn't need to import these
import pandas as pd
import sys
sys.path.append(WORK_PATH)
import tmaze #but can't import from within this file for some reason???? need setuptools
import materials
import ibex_prep
import lang_spec
import time

Mounted at /content/gdrive/
/content/mlm-scoring/src


/usr/local/lib/python3.7/dist-packages/mxnet/optimizer/optimizer.py:167: UserWarning: WARNING: New optimizer gluonnlp.optimizer.lamb.LAMB is overriding existing optimizer mxnet.optimizer.optimizer.LAMB
  Optimizer.opt_registry[name].__name__))


In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
with open(f'{WORK_PATH}/freq_bins_en_ensemble.pkl',"rb") as f:
  freq_bins = pickle.load(f)

In [ ]:
words = set()
for freq,word_lists in freq_bins.items():
  words|=set(word_lists)

In [ ]:
eng = lang_spec.lang_spec("en-US",True,WORK_PATH)

In [ ]:
eng.compile_freq_bins_and_nonwords_set()

Loading nonwords_set from pkl used by developers for en.
Loading freq_bins from pkl used by developers for en.


In [ ]:
words = set()
for freq,word_lists in eng.freq_bins.items():
  words|=set(word_lists)

In [ ]:
"wont" in words

True

In [ ]:
switch_cap = ["assange","wales"] #from 100, about even
to_delete = ["asap","copulation", "sex", "didnt","wouldnt","programmes","maximise","dude"] #eBay? more ok than LinkedIn because that's two words smushed together 
switch_cap+=["modi","bitcoin","yorker"] #from 250, about even
to_delete +=["junkie","didnt","mins","yeah"] #junkie and yeah because they're less formal? 

In [ ]:
#for 500
switch_cap += ["kyrie","china"] #indies can also refer to indpendent record labels for example
to_delete += ["dhabi","doesnt","centre"] 

In [ ]:
to_delete = ["pics","isnt","cutie","meme","ain't","stoned","auto","esque"]
switch_cap = ["incheon","potter"]

In [ ]:
eng.delete_nonwords_after(to_delete)
eng.switch_word_cap(switch_cap)

In [ ]:
eng.delete_nonwords_after(["thru"])

In [ ]:
eng.delete_nonwords_after(["whats","gonna","thats","haha"])

In [ ]:
words = set()
for freq,word_lists in eng.freq_bins.items():
  words|=set(word_lists)

In [ ]:
"dude" in words

False

In [ ]:
with open(f'{WORK_PATH}/freq_bins_en_ensemble.pkl',"wb") as f:
  pickle.dump(eng.freq_bins,f)

In [ ]:
with open(f'{WORK_PATH}/nonwords_en.pkl',"wb") as f:
  pickle.dump(eng.nonwords_set,f)

In [ ]:
with open(f'{WORK_PATH}/freq_bins_en_ensemble.pkl',"rb") as f:
  freq_bins = pickle.load(f)

In [ ]:
with open(f'{WORK_PATH}/boyce_materials_formatted.txt') as f:
    sents = f.readlines() 

In [ ]:
m_pickle_dict = {"cond_dict": "BoyceCondDict.pkl", "word_info": "BoyceWordInfo.pkl","item_pairs": "BoyceNumItemPairs.pkl"}
boyce = materials.materials(sents,";",WORK_PATH,'en',m_pickle_dict)

All pickle files already exist, loading existing pickles as opposed to creating new ones.
If you want these files overwritten, please delete one or both of them from the directory.


In [ ]:
boyce.num_item_pairs

{'1': {'relative_high': 'The son of the actress who shot himself on the set was under investigation.',
  'relative_low': 'The son of the actress who shot herself on the set was under investigation.'},
 '10': {'relative_high': 'The sister of the salesman who made a fool of herself at work was very angry.',
  'relative_low': 'The sister of the salesman who made a fool of himself at work was very angry.'},
 '101': {'practice': 'The husband of the beautiful woman bought her roses and candy for her birthday.'},
 '102': {'practice': 'The patient who the doctor treated became better after only a few treatments.'},
 '103': {'practice': 'Maya played with the blocks and the balls, but she soon got bored with them.'},
 '104': {'practice': 'The therapist set up a meeting with the upset woman and her husband yesterday.'},
 '105': {'practice': 'The reporter had dinner yesterday with the baseball player who Kevin admired.'},
 '106': {'practice': 'The visitors at the zoo watched the zookeeper who the 

In [ ]:
ctxs = [mx.gpu(0)]
model, vocab, tokenizer = get_pretrained(ctxs, 'bert-base-en-uncased')
scorer = MLMScorer(model, vocab, tokenizer, ctxs)

Vocab file is not found. Downloading.


Created scorer of class 'MLMScorer'.


In [ ]:
pickle_dict = {"freq_dict":f'{WORK_PATH}/freq_bins_en_ensemble.pkl', "word_info": f"{WORK_PATH}/BoyceWordInfo.pkl", "nonwords_set": f"{WORK_PATH}/nonwords_en.pkl", "dists_dict":f"{WORK_PATH}/EnglishDistractors.pkl"}
en_tmaze = tmaze.tmaze(scorer,'en_core_web_sm',WORK_PATH,pickle_dict)

In [ ]:
dists = {}
with open(pickle_dict['dists_dict'], "wb") as f:
  pickle.dump(dists,f)

In [ ]:
ibex_prep.create_item_groups(en_tmaze,68,boyce.num_item_pairs['68'],100,3)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[10]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be re

('[["adverb_high", 68], "Maze", {s:"Cathy will burn the wood she gathered next week, but she will save some of it.", a:"Xxxxx all bible made owned day parallel use feel one than these tried say way year."}],\n[["adverb_low", 68], "Maze", {s:"Cathy will burn the wood she gathered last week, but she will save some of it.", a:"Xxxxx all bible made owned day parallel use feel one than these tried say way year."}],',
    Distractor Index   POS Sent_Index Filler Replaced_Word Replaced_POS  \
 0        want     1  None         68  False          will           MD   
 1        also     1  None         68  False          will           MD   
 2         all     1  None         68  False          will           MD   
 3       drawn     2  None         68  False          burn           VB   
 4        fees     2  None         68  False          burn           VB   
 5       bible     2  None         68  False          burn           VB   
 6        been     3  None         68  False           the 

In [ ]:
ibex_prep.create_item_groups(en_tmaze,25,boyce.num_item_pairs['25'],100,3)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[10]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be re

('[["and_comma", 25], "Maze", {s:"The nurse examined the mother, and the child played quietly in the corner.", a:"Xxx cares streams been seems, our time I\'d rights emerged way if awards."}],\n[["and_no_comma", 25], "Maze", {s:"The nurse examined the mother and the child played quietly in the corner.", a:"Xxx cares streams been seems our time I\'d rights emerged way if awards."}],',
    Distractor Index   POS Sent_Index Filler   Replaced_Word Replaced_POS  \
 0       races     1  None         25  False           nurse           NN   
 1         bye     1  None         25  False           nurse           NN   
 2       cares     1  None         25  False           nurse           NN   
 3     convert     2  None         25  False        examined          VBD   
 4    senators     2  None         25  False        examined          VBD   
 5     streams     2  None         25  False        examined          VBD   
 6         are     3  None         25  False             the           DT  

In [ ]:
ibex_prep.create_item_groups(en_tmaze,27,boyce.num_item_pairs['27'],100,3)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[10]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[11]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[13]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be 

('[["and_comma", 27], "Maze", {s:"The tourist photographed the swimmer, and the runner got ready for the race.", a:"Xxx delete aluminium than smelled, day day didnt day June know than knows."}],\n[["and_no_comma", 27], "Maze", {s:"The tourist photographed the swimmer and the runner got ready for the race.", a:"Xxx delete aluminium than smelled day day didnt day June know than knows."}],',
       Distractor Index   POS Sent_Index Filler     Replaced_Word Replaced_POS  \
 0        delayed     1  None         27  False           tourist           NN   
 1         she'll     1  None         27  False           tourist           NN   
 2         delete     1  None         27  False           tourist           NN   
 3      bilateral     2  None         27  False      photographed          VBD   
 4   commentators     2  None         27  False      photographed          VBD   
 5      aluminium     2  None         27  False      photographed          VBD   
 6           year     3  None     

In [ ]:
english = lang_spec.lang_spec("en-US",True,WORK_PATH)

In [ ]:
english.compile_freq_bins_and_nonwords_set()

Loading nonwords_set from pkl used by developers for en.
Loading freq_bins from pkl used by developers for en.


In [ ]:
english.delete_nonwords_after(["didnt"])

In [ ]:
english.switch_word_cap(["trump's"])

In [ ]:
with open(f'{WORK_PATH}/freq_bins_en_ensemble.pkl','wb') as f:
  pickle.dump(english.freq_bins,f)

In [ ]:
with open(f'{WORK_PATH}/nonwords_en.pkl','wb') as f:
  pickle.dump(english.nonwords_set,f)

In [ ]:
ibex_prep.create_item_groups(en_tmaze,'72',boyce.num_item_pairs['72'],100,2) 

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be rem

('[["adverb_high", 72], "Maze", {s:"Kim will display the photos she took next month, but she won\'t show all of them.", a:"Xxx all crisis made you\'d year white use knew him than easy left been get way."}],\n[["adverb_low", 72], "Maze", {s:"Kim will display the photos she took last month, but she won\'t show all of them.", a:"Xxx all crisis made you\'d year white use knew him than easy left been get way."}],',
    Distractor Index   POS Sent_Index Filler Replaced_Word Replaced_POS  \
 0        need     1  None         72  False          will           MD   
 1         all     1  None         72  False          will           MD   
 2     granted     2  None         72  False       display           VB   
 3      crisis     2  None         72  False       display           VB   
 4        said     3  None         72  False           the           DT   
 5        made     3  None         72  False           the           DT   
 6       Paris     4  None         72  False        photos   

In [ ]:
start = time.time()
items_js, dist_df = ibex_prep.compile_all_sent_items_from_dict(en_tmaze,boyce.num_item_pairs,100,3)
print(time.time()-start)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be rem

Finished item 1 of 104
Finished item 2 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[17]
  str(unused_bucket_keys))


Finished item 3 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[18]
  str(unused_bucket_keys))


...

Finished item 10 of 104
Finished item 11 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[22]
  str(unused_bucket_keys))


Finished item 12 of 104
Finished item 13 of 104
Finished item 14 of 104
Finished item 15 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[24]
  str(unused_bucket_keys))


Finished item 16 of 104
Finished item 17 of 104
Finished item 18 of 104
Finished item 19 of 104
Finished item 20 of 104
Finished item 21 of 104
Finished item 22 of 104
Finished item 23 of 104
Finished item 24 of 104
Finished item 25 of 104
Finished item 26 of 104
Finished item 27 of 104
Finished item 28 of 104
Finished item 29 of 104
Finished item 30 of 104
Finished item 31 of 104
Finished item 32 of 104
Finished item 33 of 104
Finished item 34 of 104
Finished item 35 of 104
Finished item 36 of 104
Finished item 37 of 104
Finished item 38 of 104
Finished item 39 of 104
Finished item 40 of 104
Finished item 41 of 104
Finished item 42 of 104
Finished item 43 of 104
Finished item 44 of 104
Finished item 45 of 104
Finished item 46 of 104
Finished item 47 of 104
Finished item 48 of 104
Finished item 49 of 104
Finished item 50 of 104
Finished item 51 of 104
Finished item 52 of 104
Finished item 53 of 104
Finished item 54 of 104
Finished item 55 of 104
Finished item 56 of 104
Finished item 57

In [ ]:
js_to_write = ""
js_to_write+=items_js
with open(f"{WORK_PATH}/boyce_matchedDistractors.js","w") as doc:
  doc.write(js_to_write)
dist_df.to_csv(f"{WORK_PATH}/boyce100matchedDistractors.csv")

In [ ]:
to_delete = ["pics","isnt","cutie","meme","ain't","stoned","auto","esque","thru"]
switch_cap = ["incheon","potter"]

In [ ]:
js_file = f"{WORK_PATH}/boyce_matchedDistractors.js"
new_js_file = f"{WORK_PATH}/boyce_matchedDistractors_corrected.js"
ibex_prep.replace_weird_distractors(js_file,new_js_file,to_delete,dist_df,True)

In [ ]:
dist_df.loc[(dist_df["Sent_Index"] == '119') & (dist_df["Index"] == 7)]

Distractor Index   POS Sent_Index Filler Replaced_Word Replaced_POS  \
3108       bake     7  None        119   True          sued          VBD   
3109       meme     7  None        119   True          sued          VBD   
3110       isnt     7  None        119   True          sued          VBD   

            PLL   PLL_norm Number_Evaluated Best_N Ranking Rating  \
3108 -48.357280 -12.089320              100      3       3   None   
3109 -49.081090 -12.270273              100      3       2   None   
3110 -49.428914 -12.357229              100      3       1   None   

      Evaluation_Time  
3108         0.529554  
3109         0.529554  
3110         0.529554

In [ ]:
en_tmaze.freq_bins

In [ ]:
#try without fixing just to see whether fewer words like that get in there
start = time.time()
items_js, dist_df = ibex_prep.compile_all_sent_items_from_dict(en_tmaze,boyce.num_item_pairs,250,3)
print(time.time()-start)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be rem

Finished item 1 of 104
Finished item 2 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[17]
  str(unused_bucket_keys))


Finished item 3 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[18]
  str(unused_bucket_keys))


...

Finished item 10 of 104
Finished item 11 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[22]
  str(unused_bucket_keys))


Finished item 12 of 104
Finished item 13 of 104
Finished item 14 of 104
Finished item 15 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[24]
  str(unused_bucket_keys))


Finished item 16 of 104
Finished item 17 of 104
Finished item 18 of 104
Finished item 19 of 104
Finished item 20 of 104
Finished item 21 of 104
Finished item 22 of 104
Finished item 23 of 104
Finished item 24 of 104
Finished item 25 of 104
Finished item 26 of 104
Finished item 27 of 104
Finished item 28 of 104
Finished item 29 of 104
Finished item 30 of 104
Finished item 31 of 104
Finished item 32 of 104
Finished item 33 of 104
Finished item 34 of 104
Finished item 35 of 104
Finished item 36 of 104
Finished item 37 of 104
Finished item 38 of 104
Finished item 39 of 104
Finished item 40 of 104
Finished item 41 of 104
Finished item 42 of 104
Finished item 43 of 104
Finished item 44 of 104
Finished item 45 of 104
Finished item 46 of 104
Finished item 47 of 104
Finished item 48 of 104
Finished item 49 of 104
Finished item 50 of 104
Finished item 51 of 104
Finished item 52 of 104
Finished item 53 of 104
Finished item 54 of 104
Finished item 55 of 104
Finished item 56 of 104
Finished item 57

In [ ]:
js_to_write = ""
js_to_write+=items_js
with open(f"{WORK_PATH}/boyce_250matchedDistractors.js","w") as doc:
  doc.write(js_to_write)
dist_df.to_csv(f"{WORK_PATH}/boyce250matchedDistractors.csv")

In [ ]:
start = time.time()
items_js, dist_df = ibex_prep.compile_all_sent_items_from_dict(en_tmaze,boyce.num_item_pairs,500,5)
print(time.time()-start)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be rem

Finished item 1 of 104
Finished item 2 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[17]
  str(unused_bucket_keys))


Finished item 3 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[18]
  str(unused_bucket_keys))


...

Finished item 10 of 104
Finished item 11 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[22]
  str(unused_bucket_keys))


Finished item 12 of 104
Finished item 13 of 104
Finished item 14 of 104
Finished item 15 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[24]
  str(unused_bucket_keys))


Finished item 16 of 104
Finished item 17 of 104
Finished item 18 of 104
Finished item 19 of 104
Finished item 20 of 104
Finished item 21 of 104
Finished item 22 of 104
Finished item 23 of 104
Finished item 24 of 104
Finished item 25 of 104
Finished item 26 of 104
Finished item 27 of 104
Finished item 28 of 104
Finished item 29 of 104
Finished item 30 of 104
Finished item 31 of 104
Finished item 32 of 104
Finished item 33 of 104
Finished item 34 of 104
Finished item 35 of 104
Finished item 36 of 104
Finished item 37 of 104
Finished item 38 of 104
Finished item 39 of 104
Finished item 40 of 104
Finished item 41 of 104
Finished item 42 of 104
Finished item 43 of 104
Finished item 44 of 104
Finished item 45 of 104
Finished item 46 of 104
Finished item 47 of 104
Finished item 48 of 104
Finished item 49 of 104
Finished item 50 of 104
Finished item 51 of 104
Finished item 52 of 104
Finished item 53 of 104
Finished item 54 of 104
Finished item 55 of 104
Finished item 56 of 104
Finished item 57

In [ ]:
js_to_write = ""
js_to_write+=items_js
with open(f"{WORK_PATH}/boyce_500matchedDistractors.js","w") as doc:
  doc.write(js_to_write)
dist_df.to_csv(f"{WORK_PATH}/boyce500matchedDistractors.csv")

In [ ]:
pls_replace = ["heck","crap","LinkedIn","hell","Junkie","memorise","programme"]
js_file = f"{WORK_PATH}/boyce_matchedDistractors.js"
new_js_file = f"{WORK_PATH}/boyce_matchedDists_corrected.js"
ibex_prep.replace_weird_distractors(js_file,new_js_file,pls_replace,dist_df,True)

In [ ]:
with open(f"{WORK_PATH}/header.js") as doc:
  header_lines = doc.readlines()

In [ ]:
with open(f"{WORK_PATH}/boyce_sample.js", "w") as doc:
  for line in header_lines:
    doc.write(f"{line}\n")
  doc.write(items_js)
  doc.write("];")

In [ ]:
with open(f"{WORK_PATH}/boyce_matchedDists_corrected_sample.js", "w") as doc:
  for line in header_lines:
    doc.write(f"{line}\n")
  for line in items_lines:
    doc.write(f"{line}\n")
  doc.write("];")

In [ ]:
re_dist_sent = '(?:a:")(.+)(?:"})'
re.search(re_dist_sent,items[0])[1]

"Xxx all crisis made you'd year white use knew him than easy left been get way."

In [ ]:
re_item_num = "[0-9]+"
re.search(re_item_num,items[0])[0]

'72'

In [ ]:
dist_df = pd.read_csv(f"{WORK_PATH}/boyce100matchedDistractors.csv")

In [ ]:
dist_df

Unnamed: 0 Distractor  Index  POS  Sent_Index  Filler Replaced_Word  \
0              0       need      1  NaN          72   False          will   
1              1        all      1  NaN          72   False          will   
2              2    granted      2  NaN          72   False       display   
3              3     crisis      2  NaN          72   False       display   
4              4       said      3  NaN          72   False           the   
...          ...        ...    ...  ...         ...     ...           ...   
2697        2697    learned     10  NaN           2   False       wedding   
2698        2698        tax     11  NaN           2   False          felt   
2699        2699       code     11  NaN           2   False          felt   
2700        2700     stance     12  NaN           2   False      ashamed.   
2701        2701     tablet     12  NaN           2   False      ashamed.   

     Replaced_POS        PLL   PLL_norm  Number_Evaluated  Best_N  Ranking  \
0              MD -33.047848  -8.261962               100       2        2   
1              MD -35.882141 -11.960714               100       2        1   
2              VB -43.384717  -6.197817               100       2        2   
3              VB -43.562975  -7.260496               100       2        1   
4              DT -50.736954 -12.684238               100       2        2   
...           ...        ...        ...               ...     ...      ...   
2697          NaN -54.405004  -7.772143               100       2        1   
2698          NaN -55.798964 -18.599655               100       2        2   
2699          NaN -57.205256 -14.301314               100       2        1   
2700          NaN -55.155832  -9.192639               100       2        2   
2701          NaN -55.998400  -9.333067               100       2        1   

      Rating  Evaluation_Time  
0        NaN         0.213072  
1        NaN         0.213072  
2        NaN         0.214319  
3        NaN         0.214319  
4        NaN         0.216275  
...      ...              ...  
2697     NaN         1.069078  
2698     NaN         1.371531  
2699     NaN         1.371531  
2700     NaN         2.179561  
2701     NaN         2.179561  

[2702 rows x 15 columns]

In [ ]:
with open(f"{WORK_PATH}/boyce_matchedDists_sample.js", "w") as doc:
  for line in header_lines:
    doc.write(f"{line}\n")
  doc.write(items_js)
  doc.write("];")

In [ ]:
js_file = f"{WORK_PATH}/boyce_matchedDistractors.js"
new_js_file = f"{WORK_PATH}/boyce_matchedDistractors_corrected.js"
weird_dists = ["heck","crap","LinkedIn","hell","Junkie","memorise","programme"]
switch_cap = ["Lighten","oscars","modi","God's","potter","Gulf","Tokens","trump's"]
#switch capitalization of Lighten and oscars
#ibex_prep.replace_weird_distractors(js_file,new_js_file,)

In [ ]:
test = lang_spec.lang_spec("en-US", True,WORK_PATH)

In [ ]:
test.compile_freq_bins_and_nonwords_set()

Loading nonwords_set from pkl used by developers for en.
Loading freq_bins from pkl used by developers for en.


In [ ]:
test.delete_nonwords_after(["heck","crap","LinkedIn","hell","Junkie","memorise","programme"]) #don't want British spellings

In [ ]:
test.delete_nonwords_after(["lmfao"])

In [ ]:
words = set()
for freq,word_list in test.freq_bins.items():
  words|=set(word_list)

In [ ]:
for word in ["heck","crap","LinkedIn","hell","Junkie","memorise","programme"]:
  print(word in words)

False
False
False
False
False
False
False


In [ ]:
with open(f'{WORK_PATH}/freq_bins_en_ensemble.pkl','wb') as f:
  pickle.dump(test.freq_bins,f)

In [ ]:
with open(f'{WORK_PATH}/nonwords_en.pkl','wb') as f:
  pickle.dump(test.nonwords_set,f)

In [ ]:
test.switch_word_cap(switch_cap)

In [ ]:
for word in switch_cap:
  print(word in words)

False
False
True
False
True
False
False


In [ ]:
switched = ["lighten","Oscars","Modi","god's","Potter","gulf","tokens"]
for word in switched:
  print(word in words)

True
True
True
True
True
True
True


In [ ]:
new_freq_bins = test.freq_bins

In [ ]:
for freq,word_list in new_freq_bins.items():
  if any(word in switched for word in word_list):
    print(freq)

4.37
4.28
4.11
3.8
3.6
3.53
3.35


In [ ]:
from google.colab import drive
drive.mount('/content/gdrive/')
WORK_PATH = "/content/gdrive/My Drive/TMaze"
import pickle

Drive already mounted at /content/gdrive/; to attempt to forcibly remount, call drive.mount("/content/gdrive/", force_remount=True).


In [ ]:
with open(f'{WORK_PATH}/freq_bins_en_ensemble.pkl',"rb") as f:
  freq_bins = pickle.load(f)

In [ ]:
words = []
for freq,word_list in freq_bins.items():
  words+=word_list

In [ ]:
nonwords_set = {"j00","lmao","exp","mph","calif","usda","td","isis","dont","gofundme",
        "hitler","http","lgbt", "ofthe", "ncaa","https","mum","feb","mar","apr","jun","jul","aug","sept",
        "oct","nov","dec","fuckin","il","nazi","yea","huh","cock","ugh","nasa","fifa","mps","ba","sri",
        "prof","ios","bmw","l.a","opt","gosh","hon","cuz","ahh","ot","dong","bf","soo","og","tis","pres",
        "duh","shes","hes","youre","im","ive","youve","id","youd","hed","weve","dnc","umm","um","tor","eps",
        "sup","p.s","dt","sgt","phi","org","mmm","dat","ptsd","casa","yrs","cps","ooh","heck","crap","linkedin",
        "hell","junkie","memorise","programme", "lmfao","didnt","pics","isnt","cutie","meme","ain't","stoned",
        "auto","esque","thru","whats","gonna","thats","haha","asap","dhabi","doesnt","centre","mins","yeah",
        "copulation", "sex", "didnt","wouldnt","programmes","maximise","dude"}
for word in words:
  if word in nonwords_set:
    print(word) #take it out?

lmfao


In [ ]:
#could verify that it doesn't change the materials
#alternative is to take it out, though possible that it wasn't in there when we made the materials 

In [ ]:
with open(f'{WORK_PATH}/nonwords_en.pkl',"rb") as f:
  nonwords_en = pickle.load(f)

In [ ]:
for nonword in nonwords_set:
  if nonword not in nonwords_en:
    print(nonword) #lmfao in the nonwords set though

In [ ]:
names_to_capitalize = {"john","mike","lee","max","harry","sally","tony","jimmy","roger","josh","johnny","maria",
                "rick","ian","graham","ted","cooper","khan","terry","nelson","mama","bobby","batman","sid","james",
                "welsh","rogers","yang","molly","belle","sims","parsons","lea","sheila","raj","oscars","modi", "potter",
                "trump's","incheon","assange","wales","yorker","bitcoin","kyrie","china"}
only_nnp_in_context = {"financial","national","code","league","federal","trust","bank","east","west",
                "north","south","park","middle","club","military","department","board","father","mother","street","red",
                "international","house", "star","army","truth","wall","minister","box","association","sun","gun","fit",
                "master","gay","united","professor","democratic","series", "house","white","god","god's","lighten","gulf",
                "tokens"}

In [ ]:
capitalized_names = set()
for name in names_to_capitalize:
  cap_name = name[0].upper() + name[1:]
  capitalized_names.add(cap_name)

In [ ]:
for name in capitalized_names:
  if name not in words:
    print(name) #could just exclude it

Trump's


In [ ]:
"trump's" in words

True

In [ ]:
for word in only_nnp_in_context: #makes sense with this being the ensemble
  if word not in words:
    print(word)

In [ ]:
with open(f'{WORK_PATH}/new_freq_bins_en_ensemble.pkl',"wb") as f:
  pickle.dump(freq_bins,f)

In [ ]:
!pip install wordfreq

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 56.8 MB 1.2 MB/s 
     |████████████████████████████████| 53 kB 2.1 MB/s 


In [ ]:
#user_pickles = {"freq_bins": "new_freq_bins_en_ensemble.pkl", "nonwords_set": "nonwords_en.pkl"}
#fix this in code
eng = lang_spec.lang_spec("en-US",True,WORK_PATH)

In [ ]:
eng.compile_freq_bins_and_nonwords_set()

Loading nonwords_set from pkl used by developers for en.
Loading freq_bins from pkl used by developers for en.


In [ ]:
eng.delete_nonwords_after("lmfao")

In [ ]:
eng.switch_word_cap("trump's")

In [ ]:
with open(f'{WORK_PATH}/new_freq_bins_en_ensemble.pkl',"wb") as f:
  pickle.dump(eng.freq_bins,f)

In [ ]:
with open(f'{WORK_PATH}/new_nonwords_en.pkl',"wb") as f:
  pickle.dump(eng.nonwords_set,f)

In [ ]:
pickle_dict = {"freq_dict":f'{WORK_PATH}/freq_bins_en_ensemble.pkl', "word_info": f"{WORK_PATH}/BoyceWordInfo.pkl", "nonwords_set": f"{WORK_PATH}/nonwords_en.pkl", "dists_dict":f"{WORK_PATH}/EnglishDistractors.pkl"}

In [ ]:
dists = {}
with open(pickle_dict['dists_dict'], "wb") as f:
  pickle.dump(dists,f)

In [ ]:
#original
en_tmaze = tmaze.tmaze(scorer,'en_core_web_sm',WORK_PATH,pickle_dict)

In [ ]:
items_js, dist_df = ibex_prep.compile_all_sent_items_from_dict(en_tmaze,boyce.num_item_pairs,100,3)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be rem

Finished item 1 of 104
Finished item 2 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[17]
  str(unused_bucket_keys))


Finished item 3 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[18]
  str(unused_bucket_keys))


...

Finished item 12 of 104
Finished item 13 of 104
Finished item 14 of 104
Finished item 15 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[24]
  str(unused_bucket_keys))


Finished item 16 of 104
Finished item 17 of 104
Finished item 18 of 104
Finished item 19 of 104
Finished item 20 of 104
Finished item 21 of 104
Finished item 22 of 104
Finished item 23 of 104
Finished item 24 of 104
Finished item 25 of 104
Finished item 26 of 104
Finished item 27 of 104
Finished item 28 of 104
Finished item 29 of 104
Finished item 30 of 104
Finished item 31 of 104
Finished item 32 of 104
Finished item 33 of 104
Finished item 34 of 104
Finished item 35 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8, 9]
  str(unused_bucket_keys))


Finished item 36 of 104
Finished item 37 of 104
Finished item 38 of 104
Finished item 39 of 104
Finished item 40 of 104
Finished item 41 of 104
Finished item 42 of 104
Finished item 43 of 104
Finished item 44 of 104
Finished item 45 of 104
Finished item 46 of 104
Finished item 47 of 104
Finished item 48 of 104
Finished item 49 of 104
Finished item 50 of 104
Finished item 51 of 104
Finished item 52 of 104
Finished item 53 of 104
Finished item 54 of 104
Finished item 55 of 104
Finished item 56 of 104
Finished item 57 of 104
Finished item 58 of 104
Finished item 59 of 104
Finished item 60 of 104
Finished item 61 of 104
Finished item 62 of 104
Finished item 63 of 104
Finished item 64 of 104
Finished item 65 of 104
Finished item 66 of 104
Finished item 67 of 104
Finished item 68 of 104
Finished item 69 of 104
Finished item 70 of 104
Finished item 71 of 104
Finished item 72 of 104
Finished item 73 of 104
Finished item 74 of 104
Finished item 75 of 104
Finished item 76 of 104
Finished item 77

In [ ]:
pickle_dict1 = {"freq_dict":f'{WORK_PATH}/new_freq_bins_en_ensemble.pkl', "word_info": f"{WORK_PATH}/BoyceWordInfo.pkl", "nonwords_set": f"{WORK_PATH}/new_nonwords_en.pkl", "dists_dict":f"{WORK_PATH}/EnglishDistractors.pkl"}
dists = {}
with open(pickle_dict1['dists_dict'], "wb") as f:
  pickle.dump(dists,f)

In [ ]:
en_tmaze1 = tmaze.tmaze(scorer,'en_core_web_sm',WORK_PATH,pickle_dict1)
#no change to the word length bounds function

In [ ]:
items_js1, dist_df = ibex_prep.compile_all_sent_items_from_dict(en_tmaze1,boyce.num_item_pairs,100,3)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be rem

Finished item 1 of 104
Finished item 2 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[17]
  str(unused_bucket_keys))


Finished item 3 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[18]
  str(unused_bucket_keys))


...

Finished item 10 of 104
Finished item 11 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[22]
  str(unused_bucket_keys))


Finished item 12 of 104
Finished item 13 of 104
Finished item 14 of 104
Finished item 15 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[24]
  str(unused_bucket_keys))


Finished item 16 of 104
Finished item 17 of 104
Finished item 18 of 104
Finished item 19 of 104
Finished item 20 of 104
Finished item 21 of 104
Finished item 22 of 104
Finished item 23 of 104
Finished item 24 of 104
Finished item 25 of 104
Finished item 26 of 104
Finished item 27 of 104
Finished item 28 of 104
Finished item 29 of 104
Finished item 30 of 104
Finished item 31 of 104
Finished item 32 of 104
Finished item 33 of 104
Finished item 34 of 104
Finished item 35 of 104
Finished item 36 of 104
Finished item 37 of 104
Finished item 38 of 104
Finished item 39 of 104
Finished item 40 of 104
Finished item 41 of 104
Finished item 42 of 104
Finished item 43 of 104
Finished item 44 of 104
Finished item 45 of 104
Finished item 46 of 104
Finished item 47 of 104
Finished item 48 of 104
Finished item 49 of 104
Finished item 50 of 104
Finished item 51 of 104
Finished item 52 of 104
Finished item 53 of 104
Finished item 54 of 104
Finished item 55 of 104
Finished item 56 of 104
Finished item 57

In [ ]:
#first reupload tmaze to google drive
en_tmaze = tmaze.tmaze(scorer,'en_core_web_sm',WORK_PATH,pickle_dict1)

In [ ]:
items_js, dist_df = ibex_prep.compile_all_sent_items_from_dict(en_tmaze,boyce.num_item_pairs,100,3)

/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[5]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[6]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[7]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[8]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[9]
  str(unused_bucket_keys))
/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be rem

Finished item 1 of 104
Finished item 2 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[17]
  str(unused_bucket_keys))


Finished item 3 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[18]
  str(unused_bucket_keys))


...

Finished item 10 of 104
Finished item 11 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[22]
  str(unused_bucket_keys))


Finished item 12 of 104
Finished item 13 of 104
Finished item 14 of 104
Finished item 15 of 104


/usr/local/lib/python3.7/dist-packages/gluonnlp/data/sampler.py:354: UserWarning: Some buckets are empty and will be removed. Unused bucket keys=[24]
  str(unused_bucket_keys))


Finished item 16 of 104
Finished item 17 of 104
Finished item 18 of 104
Finished item 19 of 104
Finished item 20 of 104
Finished item 21 of 104
Finished item 22 of 104
Finished item 23 of 104
Finished item 24 of 104
Finished item 25 of 104
Finished item 26 of 104
Finished item 27 of 104
Finished item 28 of 104
Finished item 29 of 104
Finished item 30 of 104
Finished item 31 of 104
Finished item 32 of 104
Finished item 33 of 104
Finished item 34 of 104
Finished item 35 of 104
Finished item 36 of 104
Finished item 37 of 104
Finished item 38 of 104
Finished item 39 of 104
Finished item 40 of 104
Finished item 41 of 104
Finished item 42 of 104
Finished item 43 of 104
Finished item 44 of 104
Finished item 45 of 104
Finished item 46 of 104
Finished item 47 of 104
Finished item 48 of 104
Finished item 49 of 104
Finished item 50 of 104
Finished item 51 of 104
Finished item 52 of 104
Finished item 53 of 104
Finished item 54 of 104
Finished item 55 of 104
Finished item 56 of 104
Finished item 57

In [ ]:
dist_df.to_csv(f"{WORK_PATH}/Fixed_Word_Length_Dists.csv")

In [ ]:
items_js1 == items_js

False

In [ ]:
print(items_js)

[["adverb_high", 72], "Maze", {s:"Kim will display the photos she took next month, but she won't show all of them.", a:"x-x-x all crisis made you'd year white use knew him than easy left been get way."}],
[["adverb_low", 72], "Maze", {s:"Kim will display the photos she took last month, but she won't show all of them.", a:"x-x-x all crisis made you'd year white use knew him than easy left been get way."}],
[["adverb_high", 71], "Maze", {s:"Bob will complete the project he started next month, but Fred won't finish his.", a:"x-x-x much towards was you've off enough need hear two pole fact passed go."}],
[["adverb_low", 71], "Maze", {s:"Bob will complete the project he started last month, but Fred won't finish his.", a:"x-x-x much towards was you've off enough need hear two pole fact passed go."}],
[["adverb_high", 70], "Maze", {s:"John hired the clerk he will promote last month, but he fired another employee.", a:"x-x-x Syria it's Blair are it's staying care fun work way Asia matter purpo

In [ ]:
print(items_js1)

[["adverb_high", 72], "Maze", {s:"Kim will display the photos she took next month, but she won't show all of them.", a:"x-x-x all crisis made you'd year white use knew him than easy left been get way."}],
[["adverb_low", 72], "Maze", {s:"Kim will display the photos she took last month, but she won't show all of them.", a:"x-x-x all crisis made you'd year white use knew him than easy left been get way."}],
[["adverb_high", 71], "Maze", {s:"Bob will complete the project he started next month, but Fred won't finish his.", a:"x-x-x much towards was you've off enough need hear two pole fact passed go."}],
[["adverb_low", 71], "Maze", {s:"Bob will complete the project he started last month, but Fred won't finish his.", a:"x-x-x much towards was you've off enough need hear two pole fact passed go."}],
[["adverb_high", 70], "Maze", {s:"John hired the clerk he will promote last month, but he fired another employee.", a:"x-x-x Syria it's Blair are it's staying care fun work way Asia matter purpo

In [ ]:
eng.freq_bins

{1.01: ['aameen',
  'abadía',
  'abbildungen',
  'abdications',
  'abdulfattah',
  'aberhart',
  'abhandlung',
  'abhimaan',
  'abilit',
  'ablan',
  'aboutme',
  'absente',
  'absolutel',
  'abusable',
  'accentor',
  'accessit',
  'accouchement',
  'acetoacetyl',
  'acetylide',
  'acheh',
  'achievability',
  "achille's",
  'achillies',
  'achondrites',
  'acking',
  'acquavella',
  "acre's",
  'actioncoach',
  'activitie',
  'adamowski',
  'adao',
  'adarius',
  'addingham',
  'adefovir',
  'adenoidectomy',
  'adjured',
  'adlam',
  'admont',
  'adoula',
  "ADR's",
  'ADSI',
  'advantaging',
  'adytum',
  'adélaïde',
  'aerology',
  'aestiva',
  'afaict',
  "AFD's",
  'afdi',
  'afpfl',
  'afterman',
  'agadoo',
  'agens',
  'agganis',
  'agter',
  "agüero's",
  'ahfad',
  'ahler',
  'ahoghill',
  'aiia',
  'ainos',
  'aipmt',
  'airer',
  'airholes',
  'aironet',
  'airwalk',
  'aitai',
  'aituc',
  'ajvide',
  'akanishi',
  'akeson',
  'akhnaton',
  'akima',
  'akros',
  'akvavit'

In [ ]:
from scipy.stats import norm 

In [ ]:
 #TODO: add mean and std as parameters for init
def get_len_range(word_len,cdf_range=0.2): #using the power of statistics!
    ''' Determines the outer bounds of the length range 
    matching the word we're replacing with a distractor
    word_len = int, length of the word we're replacing with a distractor
    cdf_range = float, what percentage under the curve the length range should span
    '''
    #German
    #mean = 7.94 
    #std = 2.24
    #English
    mean = 7.26
    std = 2.28
    #TODO: add these to lang_spec class
    ppf = norm(loc=mean,scale=std).cdf(word_len)
    print(ppf)
    cdf_incr = cdf_range/2
    ppf_range = [ppf-cdf_incr, ppf+cdf_incr]
    dist_to_lower = 0
    dist_to_upper = 0
    #check if hitting lower limit
    if ppf_range[0] < 0.01:
        ppf_range[0] = 0.01
    #check if hitting upper limit
    if ppf_range[1] > 0.99: 
        ppf_range[1] = 0.99
    #lower_zscore = int(norm(loc=mean,scale=std).ppf(ppf_range[0]))
    return [int(norm(loc=mean,scale=std).ppf(ppf_range[0])),int(norm(loc=mean,scale=std).ppf(ppf_range[1]))]

In [ ]:
print(get_len_range(6))
print(get_len_range(7))
print(get_len_range(3))
print(get_len_range(10))

0.2902578567981776
[5, 6]
0.45460498943930816
[6, 7]
0.03085170243854746
[1, 4]
0.8852706485371008
[9, 12]


In [ ]:
print(get_len_range(5))

0.16078711345770824
[3, 5]


In [ ]:
experiment_dists = pd.read_csv(f"{WORK_PATH}/boyce100matchedDistractors.csv")

In [ ]:
top_exp_dists = experiment_dists.loc[experiment_dists["Ranking"] == 1]

In [ ]:
top_dists = dist_df.loc[dist_df["Ranking"] == 1]

In [ ]:
top_dists

Distractor Index   POS Sent_Index Filler Replaced_Word Replaced_POS  \
2           all     1  None         72  False          will           MD   
5        crisis     2  None         72  False       display           VB   
8          said     3  None         72  False           the           DT   
11        you'd     4  None         72  False        photos          NNS   
14         year     5  None         72  False           she          PRP   
...         ...   ...   ...        ...    ...           ...          ...   
3968      other     8  None          2  False            at         None   
3971       than     9  None          2  False           the         None   
3974    learned    10  None          2  False       wedding         None   
3977       code    11  None          2  False          felt         None   
3980     tablet    12  None          2  False      ashamed.         None   

            PLL   PLL_norm Number_Evaluated Best_N Ranking Rating  \
2    -35.882149 -11.960716              100      3       1   None   
5    -43.562984  -7.260497              100      3       1   None   
8    -50.736952 -12.684238              100      3       1   None   
11   -46.301984  -9.260397              100      3       1   None   
14   -55.095431 -13.773858              100      3       1   None   
...         ...        ...              ...    ...     ...    ...   
3968 -54.225616 -10.845123              100      3       1   None   
3971 -59.042880 -14.760720              100      3       1   None   
3974 -54.405004  -7.772143              100      3       1   None   
3977 -57.205256 -14.301314              100      3       1   None   
3980 -55.998400  -9.333067              100      3       1   None   

      Evaluation_Time  
2            5.377700  
5            0.978919  
8           11.686208  
11           0.535219  
14           6.550980  
...               ...  
3968         0.861079  
3971         1.056251  
3974         1.060583  
3977         1.265876  
3980         1.880107  

[1351 rows x 14 columns]

In [ ]:
to_exclude = pd.DataFrame(columns=["group","word_num"])

In [ ]:
diff = 0
str_combos = "c("
for i in range(len(top_exp_dists)):
  exp_row = top_dists.iloc[i]
  row = top_exp_dists.iloc[i]
  if exp_row.Distractor != row.Distractor:
    diff+=1
    group = int(exp_row.Sent_Index)
    word_num = int(exp_row.Index)
    to_exclude.loc[len(to_exclude)] = [group,word_num]
    str_combos+=f'"{group},{word_num}",'
    if int(row.Sent_Index) != group:
      print(exp_row)
      print(row)
      print(group)
      print(row.Sent_Index)
    if int(row.Index) != word_num:
      print(exp_row)
      print(row)
      print(word_num)
      print(row.Index)

In [ ]:
diff/i

0.20222222222222222

In [ ]:
to_exclude.to_csv(f"{WORK_PATH}/WordLenBugToExclude.csv")

In [ ]:
str_combos=str_combos[:-1]+")"

In [ ]:
str_combos

'c("72,3","72,14","71,5","70,3","70,9","68,3","68,5","68,15","67,3","67,5","64,3","64,4","64,6","64,9","63,7","62,3","62,9","61,3","61,5","61,11","61,13","60,3","59,3","59,5","58,10","58,11","58,13","57,1","65,4","65,6","56,3","56,5","55,4","54,4","54,6","54,12","53,4","53,14","52,1","52,2","52,4","52,8","51,2","51,4","51,9","51,11","51,12","50,5","50,6","50,12","49,10","48,3","48,5","48,6","48,11","47,2","47,7","47,12","46,11","45,8","44,3","44,10","66,4","66,10","66,13","43,2","43,8","43,10","42,5","42,8","42,9","40,2","40,4","40,5","40,6","40,7","40,13","39,3","39,4","39,9","39,10","38,3","38,6","37,5","37,6","36,2","36,7","36,13","35,1","35,2","35,5","35,10","32,3","32,6","32,12","31,5","31,8","31,10","30,2","30,3","30,4","30,9","30,10","30,11","29,7","29,11","29,13","29,15","28,1","28,4","28,7","28,11","27,1","27,2","27,4","27,5","27,6","26,1","26,3","26,5","26,9","26,11","25,2","24,12","24,14","23,3","23,4","23,11","23,13","33,3","33,4","21,4","21,8","21,11","20,1","20,4","19,2",